**If you like my notebook, please upvote my work!**

**If you use parts of this notebook in your scripts/notebooks, giving some kind of credit for instance link back to this notebook would be very much appreciated. Thanks in advance! :)**

P.S:

Please make sure that you have plotly installed on your local machine.

Thankyou! :) Hope you like my work!

In [1]:
# This Python 3 environment comes with many helpful analytics libraries installed
# It is defined by the kaggle/python Docker image: https://github.com/kaggle/docker-python
# For example, here's several helpful packages to load

import numpy as np # linear algebra
import pandas as pd # data processing, CSV file I/O (e.g. pd.read_csv)

# Input data files are available in the read-only "../input/" directory
# For example, running this (by clicking run or pressing Shift+Enter) will list all files under the input directory

import os
for dirname, _, filenames in os.walk('/kaggle/input'):
    for filename in filenames:
        print(os.path.join(dirname, filename))

# You can write up to 5GB to the current directory (/kaggle/working/) that gets preserved as output when you create a version using "Save & Run All" 
# You can also write temporary files to /kaggle/temp/, but they won't be saved outside of the current session

/kaggle/input/digit-recognizer/train.csv
/kaggle/input/digit-recognizer/test.csv
/kaggle/input/digit-recognizer/sample_submission.csv


# Importing important libraries.

In [2]:
import seaborn as sb
import plotly.express as px
import sklearn.neighbors as KNN
import plotly.graph_objects as go
import plotly.figure_factory as ff
from matplotlib import pyplot as plt
from sklearn.decomposition import PCA
from sklearn.metrics import make_scorer
from sklearn.model_selection import train_test_split

# Loading the Dataset.

In [3]:
df_train = pd.read_csv('/kaggle/input/digit-recognizer/train.csv')
df_train.describe()

label   pixel0   pixel1   pixel2   pixel3   pixel4   pixel5  \
count  42000.000000  42000.0  42000.0  42000.0  42000.0  42000.0  42000.0   
mean       4.456643      0.0      0.0      0.0      0.0      0.0      0.0   
std        2.887730      0.0      0.0      0.0      0.0      0.0      0.0   
min        0.000000      0.0      0.0      0.0      0.0      0.0      0.0   
25%        2.000000      0.0      0.0      0.0      0.0      0.0      0.0   
50%        4.000000      0.0      0.0      0.0      0.0      0.0      0.0   
75%        7.000000      0.0      0.0      0.0      0.0      0.0      0.0   
max        9.000000      0.0      0.0      0.0      0.0      0.0      0.0   

        pixel6   pixel7   pixel8  ...      pixel774      pixel775  \
count  42000.0  42000.0  42000.0  ...  42000.000000  42000.000000   
mean       0.0      0.0      0.0  ...      0.219286      0.117095   
std        0.0      0.0      0.0  ...      6.312890      4.633819   
min        0.0      0.0      0.0  ...      0.000000      0.000000   
25%        0.0      0.0      0.0  ...      0.000000      0.000000   
50%        0.0      0.0      0.0  ...      0.000000      0.000000   
75%        0.0      0.0      0.0  ...      0.000000      0.000000   
max        0.0      0.0      0.0  ...    254.000000    254.000000   

           pixel776     pixel777      pixel778      pixel779  pixel780  \
count  42000.000000  42000.00000  42000.000000  42000.000000   42000.0   
mean       0.059024      0.02019      0.017238      0.002857       0.0   
std        3.274488      1.75987      1.894498      0.414264       0.0   
min        0.000000      0.00000      0.000000      0.000000       0.0   
25%        0.000000      0.00000      0.000000      0.000000       0.0   
50%        0.000000      0.00000      0.000000      0.000000       0.0   
75%        0.000000      0.00000      0.000000      0.000000       0.0   
max      253.000000    253.00000    254.000000     62.000000       0.0   

       pixel781  pixel782  pixel783  
count   42000.0   42000.0   42000.0  
mean        0.0       0.0       0.0  
std         0.0       0.0       0.0  
min         0.0       0.0       0.0  
25%         0.0       0.0       0.0  
50%         0.0       0.0       0.0  
75%         0.0       0.0       0.0  
max         0.0       0.0       0.0  

[8 rows x 785 columns]

# Splitting the target and predictor variables.

In [4]:
df_train_x = df_train.drop('label',axis =1)
df_train_y = df_train[['label']]

# Visualising percentage variance loss.

## Fetching the variance ratios for PCA over the given dataset. 

In [5]:
pca = PCA().fit(df_train_x)
pca.explained_variance_ratio_

array([9.74893769e-02, 7.16026628e-02, 6.14590336e-02, 5.37930200e-02,
       4.89426213e-02, 4.30321399e-02, 3.27705076e-02, 2.89210317e-02,
       2.76690235e-02, 2.34887103e-02, 2.09932543e-02, 2.05900116e-02,
       1.70255350e-02, 1.69278702e-02, 1.58112641e-02, 1.48323962e-02,
       1.31968789e-02, 1.28272708e-02, 1.18797614e-02, 1.15275473e-02,
       1.07219122e-02, 1.01519930e-02, 9.64902259e-03, 9.12846068e-03,
       8.87640859e-03, 8.38766308e-03, 8.11855855e-03, 7.77405747e-03,
       7.40635116e-03, 6.86661489e-03, 6.57982211e-03, 6.38798611e-03,
       5.99367016e-03, 5.88913410e-03, 5.64335178e-03, 5.40967048e-03,
       5.09221943e-03, 4.87504936e-03, 4.75569422e-03, 4.66544724e-03,
       4.52952464e-03, 4.44989164e-03, 4.18255277e-03, 3.97505755e-03,
       3.84541993e-03, 3.74919479e-03, 3.61013219e-03, 3.48522166e-03,
       3.36487802e-03, 3.20738135e-03, 3.15467117e-03, 3.09145543e-03,
       2.93709181e-03, 2.86541339e-03, 2.80759437e-03, 2.69618435e-03,
      

In [6]:
a = []
s = 0
a.append([0,(1-s)*100,'Percentage varience lost is :'+str((1-s)*100)+'%'])
for i in range(len(pca.explained_variance_ratio_)):
    s+=pca.explained_variance_ratio_[i]
    a.append([i+1,(1-s)*100,'Percentage varience lost is : '+str((((1-s)*100)//0.0001)/10000)+'%'])
arr = pd.DataFrame(a)
arr = arr.rename(columns = {0:'No of components used:',1:'Total varience lost (in percentage)'} )
px.line(data_frame = arr,x = 'No of components used:',y = 'Total varience lost (in percentage)',
        range_x = [0,784],range_y = [0,100],hover_name = 2,
        title = 'Graph depicting the loss in varience as we reduce the number of components.')

This graph depicts how the loss in variance decreases as we increase the number of components.

1. We can see that using only 100 components we can retain almost 92% varaiance in the data
2. As we increase the number of components the variance retained increases rapidly at first and then slowly afterwords.
3. If we keep increasing the number of components, eventually the variance loss becomes 0 at 784 components.
4. We can see that if we use 300 components rather than 784 we can still retain 98.7% of the total variance therefore I have used 300 components for creating the model. 

# Visualising the effect of PCA over input images.

## Creating the image matrix for the dataset.

In [7]:
components = 300
pca = PCA(n_components = components).fit(df_train_x)
numpy_train_x = df_train_x.to_numpy()
pca_trans = pca.transform(numpy_train_x)
pca_invtrans = pca.inverse_transform(pca_trans)
row = 10
column = 7

for i in range(row):
    for j in range(column):
        if j ==0:
            a = numpy_train_x[0+(i*column)].reshape(28,28)
            a = np.pad(a, pad_width=1, mode='constant', constant_values=400)
            b = pca_invtrans[0+(i*column)].reshape(28,28)
            b = np.pad(b, pad_width=1, mode='constant', constant_values=450)
            stack = np.hstack((a,b))
        else:
            a = numpy_train_x[j+(i*column)].reshape(28,28)
            a = np.pad(a, pad_width=1, mode='constant', constant_values=400)
            b = pca_invtrans[j+(i*column)].reshape(28,28)
            b = np.pad(b, pad_width=1, mode='constant', constant_values=450)
            stack = np.hstack((stack,a))
            stack = np.hstack((stack,b))
    if i ==0:
        final = stack
    else:
        final = np.vstack((final,stack))
final = np.pad(final,pad_width=2, mode='constant', constant_values=500)
img = final

## Creating matrix of labels for the plot.

In [8]:
a = df_train_y['label'][0:row*column].to_numpy()
label = []
for i in a:
    label.append("The Label for the digit is: "+str(i))
final = []
border = ['Border']*604
final.append(border)
final.append(border)
for i in range(row):
    final.append(border)
    a = ['Border','Border']
    for j in range(column):
        for k in range(2):
            a.append('Border')
            for l in range(28):
                a.append(label[i*column+j])
            a.append('Border')
    a.append('Border')
    a.append('Border')
    for i in range(28):
        final.append(a)
    final.append(border)
final.append(border)
final.append(border)
label = final

## Plotting the image matrix.

In [9]:
fig = go.Figure(data = go.Heatmap(z = img,colorbar = None,
                                  colorscale = [[0,'black'],[0.7,'white'],[0.8,'red'],
                                                [0.9,'blue'],[1.0,'rgb(255,0,255)']],
                                  zmin = 0,zmax = 500,zauto = False,hovertext = label))
fig['layout']['yaxis']['autorange'] = "reversed"
fig.update_layout(title = 'The Distortion induced due to PCA while using '+str(components)
                  +' components.',
                  height  = 600,width = 1100,yaxis_tickvals = [0],yaxis_ticktext =[' '],
                  xaxis_tickvals = [0],xaxis_ticktext =[' '],
                  xaxis_title = 'The Original images have a red border while a blue one has been used for their PCA transforms.')
fig.update_traces(showscale = False)
fig.show()

We can therefore see that the images are very similar with no significant distortion and in some cases it might even be difficult to spot these distortions with the naked eye.

# Machine Learning Model.

## Splitting data into train and test set 

In [10]:
x_train,x_test,y_train,y_test = train_test_split(df_train_x,df_train_y,test_size = 0.1)

## Testing accuracy of the model.

In [11]:
knn = KNN.KNeighborsClassifier(n_jobs = -1,n_neighbors = 3,algorithm = 'ball_tree')
knn.fit(x_train,y_train.to_numpy().ravel())
pred = knn.predict(x_test)
pred

array([5, 7, 0, ..., 9, 7, 8])

In [12]:
y_test_np = y_test.to_numpy().ravel()
score=0
for i in range(len(y_test)):
    if pred[i] == y_test_np[i]:
        score = score+1
score /=len(y_test)
print(str(score*100))

96.66666666666667


In [13]:
predictions = pred
y_test_np = y_test.to_numpy()
classes = [0,1,2,3,4,5,6,7,8,9]


confusion_mat = np.zeros((len(classes),len(classes)))
for i in range(len(predictions)):
    confusion_mat[classes.index(predictions[i])][classes.index(y_test_np[i])]+=1
confusion_mat = confusion_mat.T
confusion_mat_norm = confusion_mat/len(y_test_np)
confusion_mat_norm = (confusion_mat_norm//0.0001)/10000

fig = ff.create_annotated_heatmap(confusion_mat_norm, x=classes, y=classes, 
                                  annotation_text=confusion_mat_norm,
                                  colorscale='Viridis',text = confusion_mat,
                                  hovertemplate='Expected Value: %{y}<br>'+
                                                'Predicted Value: %{x}<br>'+
                                                'No. of datapoints in this category are: %{text}<extra></extra>')
fig.update_layout(title_text='<b>Confusion Matrix for the dataset:</b>',
                  xaxis = {'title':'Predicted Values'},width = 900,
                  yaxis = {'title':'Expected Values','autorange':'reversed'})
fig.update_traces(showscale = True)
fig.show()

We can see that the most mistake has been made when expected label was 4 but the model predicted it as 9. This is makes sense as in the written format(not typed format) for 4 and 9 are very similar with just a small line differing at the top.

In [14]:

knn.fit(df_train_x,df_train_y)

/opt/conda/lib/python3.7/site-packages/ipykernel_launcher.py:1: DataConversionWarning:

A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().



KNeighborsClassifier(algorithm='ball_tree', leaf_size=30, metric='minkowski',
                     metric_params=None, n_jobs=-1, n_neighbors=3, p=2,
                     weights='uniform')

In [15]:
df_test = pd.read_csv('/kaggle/input/digit-recognizer/test.csv')

In [16]:
df_test['label'] = knn.predict(df_test)

In [17]:
df_test

pixel0  pixel1  pixel2  pixel3  pixel4  pixel5  pixel6  pixel7  pixel8  \
0           0       0       0       0       0       0       0       0       0   
1           0       0       0       0       0       0       0       0       0   
2           0       0       0       0       0       0       0       0       0   
3           0       0       0       0       0       0       0       0       0   
4           0       0       0       0       0       0       0       0       0   
...       ...     ...     ...     ...     ...     ...     ...     ...     ...   
27995       0       0       0       0       0       0       0       0       0   
27996       0       0       0       0       0       0       0       0       0   
27997       0       0       0       0       0       0       0       0       0   
27998       0       0       0       0       0       0       0       0       0   
27999       0       0       0       0       0       0       0       0       0   

       pixel9  ...  pixel775  pixel776  pixel777  pixel778  pixel779  \
0           0  ...         0         0         0         0         0   
1           0  ...         0         0         0         0         0   
2           0  ...         0         0         0         0         0   
3           0  ...         0         0         0         0         0   
4           0  ...         0         0         0         0         0   
...       ...  ...       ...       ...       ...       ...       ...   
27995       0  ...         0         0         0         0         0   
27996       0  ...         0         0         0         0         0   
27997       0  ...         0         0         0         0         0   
27998       0  ...         0         0         0         0         0   
27999       0  ...         0         0         0         0         0   

       pixel780  pixel781  pixel782  pixel783  label  
0             0         0         0         0      2  
1             0         0         0         0      0  
2             0         0         0         0      9  
3             0         0         0         0      9  
4             0         0         0         0      3  
...         ...       ...       ...       ...    ...  
27995         0         0         0         0      9  
27996         0         0         0         0      7  
27997         0         0         0         0      3  
27998         0         0         0         0      9  
27999         0         0         0         0      2  

[28000 rows x 785 columns]

In [18]:
a = []
for i in range(28000):
    a.append(i+1)
df_test['ImageId'] = a

In [19]:
df_test[['ImageId','label']].to_csv('submission.csv',index=False)